In [14]:
from __future__ import unicode_literals, print_function, division
from io import open
import unicodedata
import re
import random
import sys
sys.path.append("./")
import torch
import torch.nn as nn
from torch import optim
import torch.nn.functional as F

import numpy as np
from torch.utils.data import TensorDataset, DataLoader, RandomSampler

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [15]:
device

device(type='cuda')

In [16]:
SOS_token = 0
EOS_token = 1

class Lang:
    def __init__(self, name):
        self.name = name
        self.word2index = {}
        self.word2count = {}
        self.index2word = {0: "SOS", 1: "EOS"}
        self.n_words = 2  # Count SOS and EOS

    def addSentence(self, sentence):
        for word in sentence.split(' '):
            self.addWord(word)

    def addWord(self, word):
        if word not in self.word2index:
            self.word2index[word] = self.n_words
            self.word2count[word] = 1
            self.index2word[self.n_words] = word
            self.n_words += 1
        else:
            self.word2count[word] += 1

In [37]:
# Turn a Unicode string to plain ASCII, thanks to
# https://stackoverflow.com/a/518232/2809427
def unicodeToAscii(s):
    x = ''.join(
        c for c in unicodedata.normalize('NFD', s)
        if unicodedata.category(c) != 'Mn'
    )
    return x

# Lowercase, trim, and remove non-letter characters
def normalizeString(s):
    s = unicodeToAscii(s.lower().strip())
    s = re.sub(r"([.!?])", r" \1", s)
    s = re.sub(r"[^a-zA-Z!?]+", r" ", s)
    return s.strip()

In [32]:
def readLangs(lang1, lang2, reverse=False):
    print("Reading lines...")

    # Read the file and split into lines
    lines = open('data/%s-%s.txt' % (lang1, lang2), encoding='utf-8').\
        read().strip().split('\n')

    # Split every line into pairs and normalize
    pairs = [[normalizeString(s) for s in l.split('\t')] for l in lines]

    # Reverse pairs, make Lang instances
    if reverse:
        pairs = [list(reversed(p)) for p in pairs]
        input_lang = Lang(lang2)
        output_lang = Lang(lang1)
    else:
        input_lang = Lang(lang1)
        output_lang = Lang(lang2)

    return input_lang, output_lang, pairs

In [33]:
def readLangs(lang1, lang2, reverse=False):
    print("Reading lines...")

    # Read the file and split into lines
    lines = open('C:\\Users\\rjdis\\OneDrive\\Documents\\GitHub\\research\\src\\data\\translation\\eng-fra.txt', encoding='utf-8').\
        read().strip().split('\n')

    # Split every line into pairs and normalize
    pairs = [[normalizeString(s) for s in l.split('\t')] for l in lines]

    # Reverse pairs, make Lang instances
    if reverse:
        pairs = [list(reversed(p)) for p in pairs]
        input_lang = Lang(lang2)
        output_lang = Lang(lang1)
    else:
        input_lang = Lang(lang1)
        output_lang = Lang(lang2)

    return input_lang, output_lang, pairs

In [34]:
MAX_LENGTH = 10

eng_prefixes = (
    "i am ", "i m ",
    "he is", "he s ",
    "she is", "she s ",
    "you are", "you re ",
    "we are", "we re ",
    "they are", "they re "
)

def filterPair(p):
    return len(p[0].split(' ')) < MAX_LENGTH and \
        len(p[1].split(' ')) < MAX_LENGTH and \
        p[1].startswith(eng_prefixes)


def filterPairs(pairs):
    return [pair for pair in pairs if filterPair(pair)]

In [35]:
def prepareData(lang1, lang2, reverse=False):
    input_lang, output_lang, pairs = readLangs(lang1, lang2, reverse)
    print("Read %s sentence pairs" % len(pairs))
    pairs = filterPairs(pairs)
    print("Trimmed to %s sentence pairs" % len(pairs))
    print("Counting words...")
    for pair in pairs:
        input_lang.addSentence(pair[0])
        output_lang.addSentence(pair[1])
    print("Counted words:")
    print(input_lang.name, input_lang.n_words)
    print(output_lang.name, output_lang.n_words)
    return input_lang, output_lang, pairs

input_lang, output_lang, pairs = prepareData('eng', 'fra', True)
print(random.choice(pairs))

Reading lines...
go.
va !
run!
cours !
run!
courez !
wow!
ca alors !
fire!
au feu !
help!
a l'aide !
jump.
saute.
stop!
ca suffit !
stop!
stop !
stop!
arrete-toi !
wait!
attends !
wait!
attendez !
i see.
je comprends.
i try.
j'essaye.
i won!
j'ai gagne !
i won!
je l'ai emporte !
oh no!
oh non !
attack!
attaque !
attack!
attaquez !
cheers!
sante !
cheers!
a votre sante !
cheers!
merci !
get up.
leve-toi.
got it!
j'ai pige !
got it!
compris !
got it?
pige ?
got it?
compris ?
got it?
t'as capte ?
hop in.
monte.
hop in.
montez.
hug me.
serre-moi dans tes bras !
hug me.
serrez-moi dans vos bras !
i fell.
je suis tombee.
i fell.
je suis tombe.
i know.
je sais.
i left.
je suis parti.
i left.
je suis partie.
i lost.
j'ai perdu.
i'm 19.
j'ai 19 ans.
i'm ok.
je vais bien.
i'm ok.
ca va.
listen.
ecoutez !
no way!
impossible !
no way!
en aucun cas.
no way!
c'est hors de question !
no way!
il n'en est pas question !
no way!
c'est exclu !
no way!
en aucune maniere !
no way!
hors de question !
really

signe juste ici.
keep on trying.
continue d'essayer.
keep searching.
continue a chercher.
keep searching.
continuez a chercher.
kids are cruel.
les enfants sont cruels.
leave it to me.
laissez-moi m'en occuper.
leave it to me.
laisse-moi m'en charger.
leave it to us.
laissez-nous cela !
leave me alone!
fiche-moi la paix !
leave me alone!
laisse-moi seule !
leave me alone!
laisse-moi tranquille !
leave me alone!
laissez-moi tranquille !
leave me alone!
laisse-moi en paix !
leave me alone.
laisse-moi tranquille.
leave me alone.
laissez-moi tranquille.
leave me alone.
laisse-moi seule !
leave me alone.
laissez-moi tranquille !
leave me alone.
fous-moi la paix !
leave my house.
quittez ma maison !
leave my house.
quitte ma maison !
leave us alone.
fiche-nous la paix !
leave us alone.
fichez-nous la paix !
leave us alone.
laisse-nous tranquilles !
lend me a hand.
passe-moi un coup de main.
let tom answer.
laissez tom repondre.
let tom answer.
laisse tom repondre.
let tom decide.
laisse tom 

we've all seen it.
nous l'avons toutes vu.
we've all seen it.
nous l'avons toutes vue.
we've already met.
nous nous sommes deja rencontres.
we've already met.
nous nous sommes deja rencontrees.
we've been warned.
on nous a avertis.
we've been warned.
on nous a averties.
we've been warned.
nous avons ete avertis.
we've been warned.
nous avons ete averties.
we've been warned.
nous avons ete prevenus.
we've been warned.
nous avons ete prevenues.
we've been warned.
on nous a prevenus.
we've been warned.
on nous a prevenues.
we've done it all.
nous l'avons entierement fait.
we've got company.
nous avons de la compagnie.
wear warm clothes.
portez des vetements chauds.
welcome to boston.
bienvenue a boston.
were you drinking?
etais-tu en train de boire ?
were you drinking?
etiez-vous en train de boire ?
what a clever dog!
que ce chien est malin !
what a fool i was!
quel idiot j'ai ete !
what a great idea!
quelle idee brillante !
what a great idea!
quelle idee splendide !
what a great idea!
qu

no one else laughed.
personne d'autre n'a ri.
no one has anything.
personne n'a quoi que ce soit.
no one has anything.
personne ne dispose de quoi que ce soit.
no one likes losing.
personne n'aime perdre.
no one really cares.
tout le monde s'en fout.
no one really cares.
personne ne s'en soucie vraiment.
no one really knows.
personne ne le sait vraiment.
no one saw anything.
personne n'a rien vu.
no one saw anything.
personne n'a vu quoi que ce soit.
no one supported me.
personne ne m'a soutenu.
no one will help us.
personne ne nous aidera.
no one will miss me.
je ne manquerai a personne.
no one will stop us.
personne ne nous arretera.
no one will survive.
personne ne survivra.
no one would listen.
personne ne voulait ecouter.
no one would listen.
personne ne voudrait ecouter.
no one's allowed in.
personne n'est admis.
no one's allowed in.
personne n'y est admis.
no weapon was found.
aucune arme n'a ete trouvee.
no weapon was found.
aucune arme ne fut trouvee.
no, i don't want to.
non,

did anyone call me up?
est-ce que quelqu'un m'a appele ?
did he do such things?
a-t-il fait de telles choses ?
did he propose to you?
t'a-t-il demandee en mariage ?
did he stay very long?
est-il reste tres longtemps ?
did it make you angry?
cela t'a-t-il mis en colere ?
did it make you angry?
cela vous a-t-il mis en colere ?
did somebody get hurt?
quelqu'un a-t-il eu mal ?
did you ask the price?
as-tu demande le prix ?
did you ask the price?
avez-vous demande le prix ?
did you buy a new car?
avez-vous achete une voiture neuve ?
did you buy a new car?
as-tu achete une voiture neuve ?
did you buy this book?
as-tu achete ce livre ?
did you find anything?
as-tu trouve quoi que ce soit ?
did you find anything?
avez-vous trouve quoi que ce soit ?
did you get the check?
as-tu recu le cheque ?
did you get the check?
as-tu recu la note ?
did you get the check?
avez-vous recu le cheque ?
did you get the check?
avez-vous recu la note ?
did you have any luck?
as-tu reussi ?
did you have any luck?


...

elle etait trop fatiguee pour continuer a travailler.
she was watching tv when i came home.
elle regardait la television quand je suis rentre a la maison.
she whispered something into his ear.
elle murmura quelque chose a son oreille.
she will give you what money she has.
elle te donnera tout l'argent dont elle dispose.
she wore a red scarf around her neck.
elle portait, autour du cou, une echarpe rouge.
she would often come late for school.
elle arrivait souvent en retard a l'ecole.
she writes to her son every so often.
elle ecrit a son fils de temps en temps.
she's accustomed to getting up early.
elle est habituee a se lever tot.
she's been sick since last wednesday.
elle est malade depuis mercredi dernier.
she's collecting material for a book.
elle rassemble du materiel pour un livre.
she's maxed out all her credit cards.
elle a excede tous les plafonds de ses cartes de credit.
she's not confident about the future.
elle n'est pas confiante en l'avenir.
she's the breadwinner in this 

it was believed that the earth was flat.
on croyait que la terre etait plate.
it was given to me by the queen herself.
ca m'a ete remis par la reine en personne.
it was silly of him to refuse her offer.
c'etait idiot de sa part de refuser sa proposition.
it wasn't any bigger than a soccer ball.
ce n'etait pas plus gros qu'un ballon de foot.
it wasn't any bigger than a soccer ball.
elle n'etait pas plus grosse d'un ballon de foot.
it wasn't any bigger than a soccer ball.
il n'etait pas plus gros qu'un ballon de football.
it will not be long before spring comes.
l'arrivee du printemps ne tardera plus.
it'd be better if you didn't come today.
il serait preferable que vous ne veniez pas aujourd'hui.
it'd be better if you didn't come today.
il serait preferable que tu ne viennes pas aujourd'hui.
it's ok as long as it doesn't get windy.
c'est bon tant qu'il ne se met pas a venter.
it's a pity you don't know how to dance.
quel dommage que tu ne saches pas danser !
it's because of you that i'm

elle epousa un avocat new-yorkais de haut vol.
she married a hotshot lawyer from new york.
elle a epouse un avocat new-yorkais de haut vol.
she often takes advantage of his ignorance.
elle tire souvent profit de son ignorance.
she participates in many school activities.
elle prend part a beaucoup d'activites scolaires.
she prides herself on her skill in cooking.
elle est fiere de son talent culinaire.
she prides herself on her skill in cooking.
elle est fiere de ses talents culinaires.
she said nothing that would make him angry.
elle ne dit rien qui l'aurait mis en colere.
she said nothing that would make him angry.
elle n'a rien dit qui l'aurait mis en colere.
she seems to have left for tokyo yesterday.
elle semble etre partie pour tokyo hier.
she spent her life in pursuit of the truth.
elle passa sa vie a rechercher la verite.
she spent her life in pursuit of the truth.
elle a passe sa vie a rechercher la verite.
she still has a little money, but not much.
elle a encore un peu d'arge

the game was called off on account of the rain.
le match fut annule a cause de la pluie.
the garbage collector comes three times a week.
les eboueurs passent trois fois par semaine.
the girl and her parents were very sympathetic.
la fille et ses parents etaient tres sympathiques.
the girl was afraid to jump down from the roof.
la jeune fille avait peur de sauter du toit.
the girl was afraid to jump down from the roof.
la fille avait peur de sauter du toit.
the girl was visibly shaken after the accident.
la fille etait visiblement en etat de choc apres l'accident.
the groom left the bride standing at the altar.
le marie laissa la mariee devant l'autel.
the ground was covered with frost this morning.
le sol etat couvert de givre, ce matin.
the hotel was designed by a japanese architect.
cet hotel a ete concu par un architecte japonais.
the ice is not thick enough to hold our weight.
la glace n'est pas assez epaisse pour supporter notre poids.
the job of a driver is not as easy as it look

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

